# Analysis on Data on Routes

Some key questions:
1. What words are more commonly spoken about more difficult routes?
2. Can we correlate the difficulty of a route with the sentiment of the user who posted it? etc.



In [2]:
import csv
from urllib.error import HTTPError, URLError
from urllib.request import urlopen
import pickle 
import pandas as pd
import numpy as np
import datetime

import matplotlib.pyplot as plt
import seaborn as sns

import ast # for string literal eval
from bs4 import BeautifulSoup
from nltk import tokenize

from utils import pickle_load, pickle_dump 


## Loading the Data

### Routes

In [8]:
df_routes = pd.read_csv('data/routes-red-river-gorge.csv')
df_routes.drop(columns=['Unnamed: 0'], inplace=True)

In [9]:
df_routes

route_id           route_name route_grade  avg_rating num_ratings  \
0    105871977    Bedtime for Bonzo     5.6 YDS         3.4         533   
1    105880926               Eureka     5.6 YDS         3.6         694   
2    105860741  Roadside Attraction     5.7 YDS         3.8         472   
3    106085047         The Offering     5.7 YDS         2.7         453   
4    106286280           Sweet Jane    5.8- YDS         2.2         455   
..         ...                  ...         ...         ...         ...   
195  106978712              Abiyoyo   5.12b YDS         3.8         180   
196  111311288           Last Rites   5.12b YDS         3.8         159   
197  106586323       Cell Block Six   5.12c YDS         3.9         204   
198  106895798               Mosaic   5.12c YDS         3.7         152   
199  106333601           Jesus Wept   5.12d YDS         3.9         168   

      type         height num_pitches                                    FA  \
0     Trad  100 ft (30 m)   2 pitches        G. Robinson, M Hackworth, 1983   
1    Sport   70 ft (21 m)           1   Scott Hammon and James Neukam, 1999   
2     Trad  120 ft (36 m)   2 pitches                   G. Smith, R. Snider   
3    Sport   45 ft (14 m)           1   Dennis Rice, Mike Susko, Tim Powers   
4    Sport   50 ft (15 m)           1             J. J., Jane Maurer - 2004   
..     ...            ...         ...                                   ...   
195  Sport   95 ft (29 m)           1    Eric Anderson, Mark Strevels, 2005   
196  Sport  100 ft (30 m)           1  Andrew Wheatley, Mike Wheatley, 2015   
197  Sport   80 ft (24 m)           1      Brad Weaver, Kipp Trummel - 2007   
198  Sport   60 ft (18 m)           1                  Blake Bowling - 2003   
199  Sport   95 ft (29 m)           1         Tim Powers, Mike Susko - 2004   

    page_views_total  page_views_month  \
0             24,637               119   
1             23,442               113   
2             45,931               220   
3             12,095                63   
4              6,487                35   
..               ...               ...   
195            9,727                62   
196            7,263                75   
197           17,038               100   
198            7,286                46   
199           22,396               124   

                                        route_comments  \
0    [{'user_id': 'james-schroeder', 'username': 'J...   
1    [{'user_id': 'sam-stephens', 'username': 'Sam ...   
2    [{'user_id': 'chris-chaney', 'username': 'Chri...   
3    [{'user_id': 'saxfiend', 'username': 'saxfiend...   
4    [{'user_id': 'mark-kauzlarich', 'username': 'M...   
..                                                 ...   
195  [{'user_id': 'steven-kovalenko', 'username': '...   
196  [{'user_id': 'jessi-h', 'username': 'Jessi H',...   
197  [{'user_id': 'j-tot', 'username': 'J tot', 'bo...   
198  [{'user_id': 'curt-macneill', 'username': 'Cur...   
199  [{'user_id': 'curt-macneill', 'username': 'Cur...   

                                           Description  \
0    A great route normally done as 2 short pitches...   
1    Can you say vertical jug climbing? This route ...   
2    A beautiful dihedral crack.  Scramble to a led...   
3    This route traverses right. Don't Take Yer Gun...   
4    Formerly one of the few interesting trad lines...   
..                                                 ...   
195  Beautiful line climbing out the overhanging or...   
196  Shares a start with Diminished Gluteal Syndrom...   
197  Starts in a dihedral-like crack slowly making ...   
198  Mosaic climbs the right side of the obvious ov...   
199  Starts at the right side of the big steep wall...   

                                       Permit Required  \
0                                                  NaN   
1                                                  NaN   
2    ***Climbers MUST NOT climb at GFNP without a d...   
3                        

### Manufacturing Comment Dataframe

In [15]:
df_comments = pd.DataFrame()
for i in range(len(df_routes)):
    df_comments = pd.concat([df_comments, pd.DataFrame(ast.literal_eval(df_routes.route_comments[i]))], axis=0)


In [18]:
df_comments

user_id         username  \
0   james-schroeder  James Schroeder   
1            tony-b           Tony B   
2        adam-steel       Adam Steel   
3      travis-melin     Travis Melin   
4          saxfiend         saxfiend   
..              ...              ...   
1     dylan-randall    Dylan Randall   
2        brie-abram       Brie Abram   
3   chris-smallwood  Chris Smallwood   
4      nathan-devan     Nathan Devan   
5       cris-garcia      Cris Garcia   

                                                 body            hometown  
0   This is a great route, I had a great time on i...    Fort Collins, CO  
1   A good route with good sections, but it always...  Around Boulder, CO  
2   This route was overhyped for me and has the sa...      Salt Lake City  
3    cool finish, liked the exposure \n\nNov 15, 2007        Portland, OR  
4   Short pitches, but an excellent route with nic...         Decatur, GA  
..                                                ...                 ...  
1   Really, this climb is something incredible. Ev...       Nashville, TN  
2   This route is incredible. If this grade is har...            Celo, NC  
3                vimeo.com/245977683 \n\nApr 20, 2018                      
4               youtu.be/XhJOAtUSuKU \n\nNov 29, 2020      Huntsville, AL  
5   Soft or not this one was fun! If you can recov...            Michigan  

[2248 rows x 4 columns]

### Ticks / Ratings / Stars Data

In [141]:
df_ticks = pd.read_csv('data/ticks/ticks.csv')
df_ratings = pd.read_csv('data/ticks/ratings.csv')
df_stars = pd.read_csv('data/ticks/stars.csv')


In [142]:
# cleaning ticks dataframe
df_ticks.fillna('', inplace=True)
df_ticks = df_ticks[((df_ticks.user != '') & (df_ticks.user != 'False'))]
df_ticks['user_id'] = [ast.literal_eval(df_ticks.user.iloc[i])['id'] for i in range(len(df_ticks))]
df_ticks['user_name'] = [ast.literal_eval(df_ticks.user.iloc[i])['name'] for i in range(len(df_ticks))]
df_ticks.drop(columns=['user'], inplace=True)


/tmp/ipykernel_160151/3635791633.py:2: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_ticks.fillna('', inplace=True)


In [143]:
df_ticks.head()

id                    date comment style leadStyle  pitches  \
0  125247893   Nov 1, 2023, 12:00 am          Lead   Onsight        1   
1  125242407  Oct 31, 2023, 12:00 am          Lead   Onsight        2   
2  125247393  Oct 31, 2023, 12:00 am          Lead     Flash        2   
3  125235727  Oct 30, 2023, 12:00 am          Lead  Redpoint        2   
4  125229486  Oct 29, 2023, 12:00 am            TR                  2   

                                                text  \
0    &middot; 1 pitch.  Lead / Onsight. led pitch 1.   
1                         &middot;  Lead / Onsight.    
2                           &middot;  Lead / Flash.    
3   &middot;  Lead / Redpoint. Led first pitch. J...   
4                                     &middot;  TR.    

                     createdAt                    updatedAt    user_id  \
0  2023-11-02T00:43:33.000000Z  2023-11-02T00:43:33.000000Z  201100043   
1  2023-10-31T18:57:56.000000Z  2023-10-31T18:57:56.000000Z  200160322   
2  2023-11-01T22:56:24.000000Z  2023-11-01T22:56:24.000000Z  200376514   
3  2023-10-30T06:09:48.000000Z  2023-10-30T06:09:48.000000Z  200597713   
4  2023-10-29T16:38:44.000000Z  2023-10-29T16:38:44.000000Z  201702876   

       user_name  
0   Josh Piccoli  
1  Jared Hancock  
2  John Milligan  
3        N Klick  
4    Dave Shaerf

### Collecting user_ids and mapping it to the username_ids.

In [ ]:
user_id_tags_map = {}

In [94]:
base = 'https://www.mountainproject.com/user'

for i in range(len(df_ticks)):
    print(f'{i} of {len(df_ticks)}')
    user_id = df_ticks.iloc[i].user_id
    if user_id not in user_id_tags_map:
        url = f'{base}/{user_id}'
        try:
            html = urlopen(url)
            user_id_tags_map.update({user_id: html.url.split('/')[-1]})
        except (HTTPError, URLError) as e:
            print(f'Error: {e.reason}')

pickle.dump(user_id_tags_map, open('data/pickles/user_id_tags_map.pkl', 'wb'))

0 of 166584
1 of 166584
2 of 166584
3 of 166584
4 of 166584
5 of 166584
6 of 166584
7 of 166584
8 of 166584
9 of 166584
10 of 166584
11 of 166584
12 of 166584
13 of 166584
14 of 166584
15 of 166584
16 of 166584
17 of 166584
18 of 166584
19 of 166584
20 of 166584
21 of 166584
22 of 166584
23 of 166584
24 of 166584
25 of 166584
26 of 166584
27 of 166584
28 of 166584
29 of 166584
30 of 166584
31 of 166584
32 of 166584
33 of 166584
34 of 166584
35 of 166584
36 of 166584
37 of 166584
38 of 166584
39 of 166584
40 of 166584
41 of 166584
42 of 166584
43 of 166584
44 of 166584
45 of 166584
46 of 166584
47 of 166584
48 of 166584
49 of 166584
50 of 166584
51 of 166584
52 of 166584
53 of 166584
54 of 166584
55 of 166584
56 of 166584
57 of 166584
58 of 166584
59 of 166584
60 of 166584
61 of 166584
62 of 166584
63 of 166584
64 of 166584
65 of 166584
66 of 166584
67 of 166584
68 of 166584
69 of 166584
70 of 166584
71 of 166584
72 of 166584
73 of 166584
74 of 166584
75 of 166584
76 of 166584
77 of 166

In [147]:
username_to_userid

{'josh-piccoli': 201100043,
 'jared-hancock': 200160322,
 'john-milligan': 200376514,
 'nicholas-k': 200597713,
 'dave-shaerf': 201702876,
 'joey-eberline': 200222082,
 'meredith-soeder': 201182561,
 'dan-smee': 201450182,
 'don-seanor': 200852739,
 'tasha-p': 200189233,
 'wendy-williams': 109097895,
 'attila': 106656735,
 'jeremy-moritz': 201003390,
 'joe-berusch': 201374297,
 'mark-scott': 110455750,
 'lauren-errichiello': 200870363,
 'rowan-stalnaker': 201276038,
 'david-p': 200793667,
 'elissa-frankel': 201556327,
 'leo-allen': 201345851,
 'jordan-giuliano': 201300708,
 'patrick-deegan': 200002278,
 'kevin-huang': 200399096,
 'kyle-suver': 200408822,
 'sara-schwabe': 200564785,
 'willow-jordan': 201359804,
 'emily-claeys': 201570853,
 'aidan-brennan': 201242996,
 'dave-irving': 201463879,
 'bobby-tre': 201464927,
 'quinn-keitel': 200689473,
 'ruben-santana': 201521628,
 'mackenzie-c': 111899379,
 'marco-soto': 200693749,
 'michael-mckinney': 200513307,
 'samantha-hochevar': 2009308

In [104]:
username_to_userid = {v: k for k, v in user_id_tags_map.items()}
df_comments['user_id'] = [username_to_userid.get(df_comments.iloc[i].username_id, '') for i in range(len(df_comments))]

In [148]:
df_ticks['username_id'] = [user_id_tags_map.get(df_ticks.iloc[i]['user_id'], '') for i in range(len(df_ticks))]

In [150]:
df_ticks.to_csv('data/ticks/ticks-clean.csv')

In [140]:
user_id

106389235

In [139]:
user_id_tags_map

{201100043: 'josh-piccoli',
 200160322: 'jared-hancock',
 200376514: 'john-milligan',
 200597713: 'nicholas-k',
 201702876: 'dave-shaerf',
 200222082: 'joey-eberline',
 201182561: 'meredith-soeder',
 201450182: 'dan-smee',
 200852739: 'don-seanor',
 200189233: 'tasha-p',
 109097895: 'wendy-williams',
 106656735: 'attila',
 201003390: 'jeremy-moritz',
 201374297: 'joe-berusch',
 110455750: 'mark-scott',
 200870363: 'lauren-errichiello',
 201276038: 'rowan-stalnaker',
 200793667: 'david-p',
 201556327: 'elissa-frankel',
 201345851: 'leo-allen',
 201300708: 'jordan-giuliano',
 200002278: 'patrick-deegan',
 200399096: 'kevin-huang',
 200408822: 'kyle-suver',
 200564785: 'sara-schwabe',
 201359804: 'willow-jordan',
 201570853: 'emily-claeys',
 201242996: 'aidan-brennan',
 201463879: 'dave-irving',
 201464927: 'bobby-tre',
 200689473: 'quinn-keitel',
 201521628: 'ruben-santana',
 201695588: 'mackenzie-c',
 200693749: 'marco-soto',
 200513307: 'michael-mckinney',
 200930898: 'samantha-hocheva

In [138]:
df_ticks['id']

0         125247893
1         125242407
2         125247393
3         125235727
4         125229486
            ...    
176483    107034672
176484    118742952
176485    107198031
176486    106333618
176487    109541566
Name: id, Length: 166584, dtype: int64

In [114]:
df_ticks.user_id.value_counts()

user_id
    166584
Name: count, dtype: int64

In [109]:
df_comments.user_id.value_counts()

user_id
             812
108320835     46
112505301     42
109188550     36
113051621     28
            ... 
200718908      2
200681881      2
107472859      2
200910215      2
106045498      2
Name: count, Length: 355, dtype: int64

In [ ]:
df